In [3]:
# compile
data = {}

import h5py 
import numpy

In [4]:
# collect coincs
d = {}
for cfile in ['o1o2o3a_coincs.hdf', 'o3b_coincs.hdf']:
    f = h5py.File(cfile, 'r')
    for k in f:
        if k not in d:
            d[k] = []
        d[k] += [f[k][:]]
        
for k in d:
    d[k] = numpy.concatenate(d[k])

In [5]:
import numpy
# collect singles
data = [d]

for ifo in ['H1', 'L1']:
    for run in ['bns', 'bbh', 'nsbh']:
        d2 = {}
        f = h5py.File('./{}_{}_trigs.hdf'.format(run, ifo), 'r')
        
        d2['{}_chisq'.format(ifo)] = f['chisq'][:]
        d2['{}_sg_chisq'.format(ifo)] = f['sg_chisq'][:]
        d2['{}_snr'.format(ifo)] = f['snr'][:]
        d2['stat'] = f['stat'][:]
        tid = f['tid'][:]
        d2['{}_end_time'.format(ifo)] =f['time'][:]

        b = h5py.File('{}.hdf'.format(run), 'r')
        d2['mass1'] = b['mass1'][:][tid]
        d2['mass2'] = b['mass2'][:][tid]
        d2['spin1z'] = b['spin1z'][:][tid]
        d2['spin2z'] = b['spin2z'][:][tid]
        d2['ifar'] = numpy.ones(len(tid)) * -1
        
        for ifo2 in ['H1', 'L1', 'V1']:
            if ifo != ifo2:
                for k in ['{}_snr', '{}_end_time', '{}_sg_chisq', '{}_chisq']:
                    d2[k.format(ifo2)] = numpy.ones(len(tid)) * -1
                
        data.append(d2)

In [6]:
com = {}

for k in data[0]:
    com[k] = numpy.concatenate([d[k] for d in data])
    print(k, len(com[k]))

H1_chisq 7210792
H1_end_time 7210792
H1_sg_chisq 7210792
H1_snr 7210792
L1_chisq 7210792
L1_end_time 7210792
L1_sg_chisq 7210792
L1_snr 7210792
V1_chisq 7210792
V1_end_time 7210792
V1_sg_chisq 7210792
V1_snr 7210792
ifar 7210792
mass1 7210792
mass2 7210792
spin1z 7210792
spin2z 7210792
stat 7210792


In [7]:
t1 = com['H1_end_time']
t2 = com['L1_end_time']
t3 = com['V1_end_time']

c = (t1 != -1).astype(int) + (t2 != -1).astype(int) + (t3 != -1).astype(int)

atime = numpy.zeros(len(t1))
atime[t1 != -1] += t1[t1 != -1]
atime[t2 != -1] += t2[t2 != -1]
atime[t3 != -1] += t3[t3 != -1]
atime /= c
com['time'] = atime

In [8]:
# cluster events and adjust far if needed
s = com['time'].argsort()
for k in com:
    com[k] = com[k][s]
    
l = numpy.searchsorted(com['time'], com['time'] - .1)
r = numpy.searchsorted(com['time'], com['time'] + .1)
dup = numpy.where(r-l > 1)[0]
li = l[dup]
ri = r[dup]
loc = numpy.zeros(len(li), dtype=[('l', int), ('r', int)])
loc['l'] = li
loc['r'] = ri
loc = numpy.unique(loc)

keep = numpy.ones(len(s), dtype=bool)

for v in loc:
    l, r = v['l'], v['r']
    ifar = numpy.array(com['ifar'][l:r], ndmin=1)

    kv1 = numpy.where(ifar == -1)[0]
    kv2 = ifar.argmax()
    if len(kv1) == 0:
        kv = kv2
    else:
        kv1 = kv1[0]
        if ifar[kv2] > 0.01:
            kv = kv2
        else:
            kv = kv1
        
    kv = l + kv
    keep[l:r] = 0
    keep[kv] = 1  

In [9]:
from pycbc.dq import query_flag

com2 = {k: com[k][keep] for k in com}

segs = {'H1':[], 'L1':[], 'V1':[]}
for ifo in ['H1', 'L1', 'V1']:
    for s, e in [(1126051217, 1137254417), (1164556817, 1187733618), (1238166018, 1253977218),  (1253977219, 1320363336)]:
        if ifo == 'V1' and s == 1126051217:
            continue
        segs[ifo] +=  query_flag(ifo, 'DATA', s, e, cache=True)


In [10]:
from astropy.time import Time
ons = []
trigs = []
names = []

dt = Time(com2['time'], scale='utc', format='gps').datetime

for i, t in enumerate(com2['time']):
    on = ''
    trig = ''
    for ifo in ['H', 'L', 'V']:
        if t in segs[ifo + '1']:
            on += ifo
        if com2['{}1_end_time'.format(ifo)][i] != -1:
            trig += ifo
            
    ons.append(on)
    trigs.append(trig)
    
    name = '{:02d}{:02d}{:02d}_{:02d}{:02d}{:02d}'.format(dt[i].year - 2000,
                                                          dt[i].month,
                                                          dt[i].day, dt[i].hour,
                                                          dt[i].minute, dt[i].second)

    names.append(name)
    if i % 100000 == 0:
        print(i)
    
ons = numpy.array(ons)
trigs = numpy.array(trigs)
names = numpy.array(names)
com2['obs'] = ons
com2['trig'] = trigs
com2['name'] = names

0
100000
200000
300000
400000
500000
600000
700000
800000
900000
1000000
1100000
1200000
1300000
1400000
1500000
1600000
1700000
1800000
1900000
2000000
2100000
2200000
2300000
2400000
2500000
2600000
2700000
2800000
2900000
3000000
3100000
3200000
3300000
3400000
3500000
3600000
3700000
3800000
3900000
4000000
4100000
4200000
4300000
4400000
4500000
4600000
4700000
4800000
4900000
5000000
5100000
5200000
5300000
5400000
5500000
5600000
5700000
5800000
5900000
6000000
6100000
6200000
6300000
6400000
6500000
6600000


In [11]:
pastro = numpy.ones(len(com2['obs'])) * -1

for ifo in ['L1', 'H1']:
    f = h5py.File('./pastro_{}_bbh_single.hdf'.format(ifo), 'r')
    p = f['pastro'][:]
    t = f['time'][:]
    
    for tv, pv in zip(t, p):
        if pv != 0:
            l = abs(com2['time'] - tv).argmin()
            pastro[l] = pv
            print(pv, Time(tv, scale='utc', format='gps').datetime)
            
d = numpy.loadtxt('coinc_pastro.txt', dtype=str)

for tv, pv in zip(d[:,0], d[:,-1]):
    tv = float(tv)
    pv = float(pv)
    if pv != 0:
        l = abs(com2['time'] - tv).argmin()
        pastro[l] = pv
        
from pycbc.catalog import Merger
t = Merger("GW190425", source='gwtc-2').time
l = abs(com2['time'] - t).argmin()
pastro[l] = 0.5

#t = Merger("GW190425", source='gwtc-3').time
#GW200105_162426
t = 1262276684
l = abs(com2['time'] - t).argmin()
pastro[l] = 0.5
#com2['ifar'][l] = 0.29
    
com2['pastro'] = pastro

0.5267138285071004 2019-04-24 18:06:48.141113
0.7253716313269517 2019-06-20 03:04:21.311523
0.7294236501314261 2019-07-08 23:24:57.384277
0.7713819343981927 2019-09-10 11:28:07.323730
0.7841108062679302 2020-01-12 15:58:38.090820
0.6582035575226363 2020-03-02 01:58:11.518066


In [12]:
k = ((com2['pastro'] >= 0.5) | (com2['ifar'] > 10))

print(k.sum())
l = numpy.where(k)[0]
for i in l:
    print(com2['name'][i], com2['time'][i], com2['ifar'][i], com2['pastro'][i], com2['obs'][i], com2['trig'][i], com2['mass1'][i])

94
150914_095045 1126259462.4257812 65506.27452309427 1.0 HL HL 35.98605337859872
151012_095443 1128678900.4450684 3589.1036165038686 1.0 HL HL 16.196153701610022
151226_033853 1135136350.649414 59198.64683277562 1.0 HL HL 4.163723947145793
170104_101158 1167559936.6000977 72943.96475809313 1.0 HL HL 26.636831037358768
170121_212536 1169069154.5761719 64.43813141174304 1.0 HL HL 39.96648288604893
170202_135657 1170079035.732666 2.0085444114055724 0.86 HL HL 27.516420922875838
170304_163753 1172680691.3659668 0.9958084048789108 0.74 HL HL 46.90803236543879
170403_230611 1175295989.2316895 0.985606084479302 0.72 HL HL 60.93375460639748
170608_020116 1180922494.4887695 910.7101217412392 1.0 L HL 13.059284424633564
170727_010430 1185152688.0332031 287.77916366494895 1.0 HL HL 46.90803236543879
170729_185629 1185389807.3237305 113.79764308504767 1.0 HL HL 39.09494399289268
170809_082821 1186302519.75 12908.003372355206 1.0 HLV HL 40.074714133399596
170814_103043 1186741861.5336914 21083.491

In [14]:
# TODO: need to fix up 170608 obs, 
# and 190814 *all* values
com3 = {}
for k in com2:
    com3[k] = com2[k].copy()
    
com3['ifar'][com3['ifar'] != -1] /= 4.0

k = ((com3['pastro'] >= 0.5) | (com3['ifar'] > 100))

print(k.sum())
l = numpy.where(k)[0]
for i in l:
    print(com3['name'][i], com3['time'][i], com3['ifar'][i], 
          com3['pastro'][i], com3['obs'][i], com3['trig'][i], com3['mass1'][i], com3['mass2'][i])

    
o = h5py.File('./4-ogc.hdf', 'w')
for k in com3:
    d = com3[k]
    if d.dtype.kind == 'U':
        d = d.astype(bytes)
    else:
        d = d.astype(numpy.float64)

    o.create_dataset(k, data=d,  compression="gzip", shuffle=True)
    
i = numpy.where(o['name'][:] == '190814_211039'.encode())[0][0]

hsnr, hchisq, hsg_chisq = 10.973093, 1.5333716351052988, 1.0
lsnr, lchisq, lsg_chisq = 21.060415, 1.3381044968314793, 1.0

o['obs'][i] = 'HLV'
o['H1_snr'][i] = hsnr
o['H1_chisq'][i] = hchisq
o['H1_sg_chisq'][i] = hsg_chisq
o['L1_snr'][i] = lsnr
o['L1_chisq'][i] = lchisq
o['L1_sg_chisq'][i] = lsg_chisq

i = numpy.where(o['name'][:] == '170608_020116'.encode())[0][0]
o['obs'][i] = 'HL'
o.close()

94
150914_095045 1126259462.4257812 16376.568630773567 1.0 HL HL 35.98605337859872 27.371181692623153
151012_095443 1128678900.4450684 897.2759041259671 1.0 HL HL 16.196153701610022 28.052870127738228
151226_033853 1135136350.649414 14799.661708193906 1.0 HL HL 4.163723947145793 37.40002120970358
170104_101158 1167559936.6000977 18235.991189523284 1.0 HL HL 26.636831037358768 27.294216789846384
170121_212536 1169069154.5761719 16.10953285293576 1.0 HL HL 39.96648288604893 20.360204374243754
170202_135657 1170079035.732666 0.5021361028513931 0.86 HL HL 27.516420922875838 32.481259939001944
170304_163753 1172680691.3659668 0.2489521012197277 0.74 HL HL 46.90803236543879 49.206140508746344
170403_230611 1175295989.2316895 0.2464015211198255 0.72 HL HL 60.93375460639748 81.14824653815194
170608_020116 1180922494.4887695 227.6775304353098 1.0 L HL 13.059284424633564 7.4323408172188214
170727_010430 1185152688.0332031 71.94479091623724 1.0 HL HL 46.90803236543879 49.206140508746344
170729_18